In [1]:
import subprocess
import sys
import os
import shutil
from pathlib import Path

# Environment setup (copied from 01_quick_baseline.ipynb)
print(subprocess.run(['bash', '-lc', 'nvidia-smi || true'], capture_output=True, text=True).stdout)

# Sanity check first: try to import and verify torch
try:
    import torch
    print('torch:', torch.__version__, 'built CUDA:', getattr(torch.version, 'cuda', None))
    print('CUDA available:', torch.cuda.is_available())
    assert str(getattr(torch.version,'cuda','')).startswith('12.1'), f'Wrong CUDA build: {torch.version.cuda}'
    assert torch.cuda.is_available(), 'CUDA not available'
    print('GPU:', torch.cuda.get_device_name(0))
    
    import torchvision
    print('torchvision version:', torchvision.__version__)
    assert torchvision.__version__.startswith('0.19.1+cu121'), f'Wrong torchvision version: {torchvision.__version__}'
    
    print('Environment already correctly set up, skipping installation.')
    skip_install = True
except (ImportError, AssertionError) as e:
    print(f'Environment check failed: {e}. Proceeding with clean install.')
    skip_install = False

def pip(*args):
    if skip_install:
        print('Skipping pip command due to good environment.')
        return
    print('>', *args, flush=True)
    subprocess.run([sys.executable, '-m', 'pip', *args], check=True)

# Only do clean install if needed
if not skip_install:
    # 0) Hard reset any prior torch stacks
    for pkg in ('torch','torchvision','torchaudio'):
        subprocess.run([sys.executable, '-m', 'pip', 'uninstall', '-y', pkg], check=False)

    # Clean stray site dirs
    for d in (
        '/app/.pip-target/torch',
        '/app/.pip-target/torch-2.8.0.dist-info',
        '/app/.pip-target/torch-2.4.1.dist-info',
        '/app/.pip-target/torchvision',
        '/app/.pip-target/torchvision-0.23.0.dist-info',
        '/app/.pip-target/torchvision-0.19.1.dist-info',
        '/app/.pip-target/torchaudio',
        '/app/.pip-target/torchaudio-2.8.0.dist-info',
        '/app/.pip-target/torchaudio-2.4.1.dist-info',
        '/app/.pip-target/torchgen',
        '/app/.pip-target/functorch',
    ):
        if os.path.exists(d):
            print('Removing', d)
            shutil.rmtree(d, ignore_errors=True)

    # 1) Install the EXACT cu121 torch stack FIRST
    pip('install',
        '--index-url', 'https://download.pytorch.org/whl/cu121',
        '--extra-index-url', 'https://pypi.org/simple',
        'torch==2.4.1', 'torchvision==0.19.1', 'torchaudio==2.4.1')

    # 2) Create a constraints file
    Path('constraints.txt').write_text(
        'torch==2.4.1\n'
        'torchvision==0.19.1\n'
        'torchaudio==2.4.1\n'
    )

    # 3) Install NON-torch deps
    pip('install', '-c', 'constraints.txt',
        'numpy', 'scipy', 'pandas', 'Pillow', 'opencv-python-headless', 'scikit-learn', 'tqdm',
        '--upgrade-strategy', 'only-if-needed')

# 4) Final sanity gate
import torch
print('torch:', torch.__version__, 'built CUDA:', getattr(torch.version, 'cuda', None))
print('CUDA available:', torch.cuda.is_available())
assert str(getattr(torch.version,'cuda','')).startswith('12.1'), f'Wrong CUDA build: {torch.version.cuda}'
assert torch.cuda.is_available(), 'CUDA not available'
print('GPU:', torch.cuda.get_device_name(0))

import torchvision
print('torchvision version:', torchvision.__version__)

# Fix for OpenCV if needed
try:
    import cv2
    print('OpenCV imported successfully:', cv2.__version__)
except ImportError as e:
    print(f'OpenCV import failed: {e}. Installing headless version.')
    subprocess.run([sys.executable, '-m', 'pip', 'uninstall', '-y', 'opencv-python', 'opencv-contrib-python'], check=False)
    subprocess.run([sys.executable, '-m', 'pip', 'install', '-c', 'constraints.txt', 'opencv-python-headless'], check=True)
    import cv2
    print('OpenCV headless installed and imported:', cv2.__version__)

Sun Sep 28 11:43:47 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.144.06             Driver Version: 550.144.06     CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA A10-24Q                 On  |   00000002:00:00.0 Off |                    0 |
| N/A   N/A    P0             N/A /  N/A  |     414MiB /  24512MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

torchvision version: 0.19.1+cu121
Environment already correctly set up, skipping installation.
torch: 2.4.1+cu121 built CUDA: 12.1
CUDA available: True
GPU: NVIDIA A10-24Q
torchvision version: 0.19.1+cu121
OpenCV imported successfully: 4.11.0


In [2]:
import json
import pandas as pd
import numpy as np
from collections import Counter
import torch
from torch.utils.data import Dataset, DataLoader
import torchvision.transforms as T
from PIL import Image
import cv2
import os
from tqdm import tqdm
from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score

# Load train and test metadata
with open('nybg2020/train/metadata.json', 'r') as f:
    train_meta = json.load(f)
train_images = train_meta['images']
train_annotations = train_meta['annotations']
train_df = pd.DataFrame(train_images)
annotations_df = pd.DataFrame(train_annotations)
train_df = train_df.merge(annotations_df, left_on='id', right_on='image_id', how='left')
# Fix column name after merge: rename 'id_x' to 'id'
train_df = train_df.rename(columns={'id_x': 'id'})
print('Train shape:', train_df.shape)
print('Train columns:', list(train_df.columns))

with open('nybg2020/test/metadata.json', 'r') as f:
    test_meta = json.load(f)
test_images = test_meta['images']
test_df = pd.DataFrame(test_images)
print('Test shape:', test_df.shape)
print('Test columns:', list(test_df.columns))

# Tight crop function (non-white crop, pad, BGR2RGB, fallback)
def tight_crop(path_or_img, white_thresh=240, pad_ratio=0.02):
    import cv2, numpy as np
    if isinstance(path_or_img, str):
        img = cv2.imread(path_or_img)  # BGR
    else:
        img = path_or_img
    if img is None:
        # safe fallback
        return np.zeros((100, 100, 3), dtype=np.uint8)
    gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
    _, mask = cv2.threshold(gray, white_thresh, 255, cv2.THRESH_BINARY_INV)
    coords = cv2.findNonZero(mask)
    if coords is not None:
        x, y, w, h = cv2.boundingRect(coords)
        pad = int(round(pad_ratio * min(img.shape[:2])))
        x0 = max(0, x - pad); y0 = max(0, y - pad)
        x1 = min(img.shape[1], x + w + pad); y1 = min(img.shape[0], y + h + pad)
        crop = img[y0:y1, x0:x1]
    else:
        crop = img
    crop = cv2.cvtColor(crop, cv2.COLOR_BGR2RGB)
    return crop

# Transforms (384px for speed)
transform = T.Compose([
    T.Lambda(lambda p: tight_crop(p)),
    T.ToPILImage(),
    T.Resize(416),
    T.CenterCrop(384),
    T.ToTensor(),
    T.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

flip_transform = T.Compose([
    T.Lambda(lambda p: tight_crop(p)),
    T.ToPILImage(),
    T.Resize(416),
    T.CenterCrop(384),
    T.RandomHorizontalFlip(p=1.0),  # deterministic flip
    T.ToTensor(),
    T.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

# Custom Dataset
class HerbariumDataset(Dataset):
    def __init__(self, df, root_dir, transform=None):
        self.df = df
        self.root_dir = root_dir
        self.transform = transform
        self.file_names = df['file_name'].values
        self.ids = df['id'].values
        self.category_ids = df['category_id'].values if 'category_id' in df.columns else None

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        file_name = self.file_names[idx]
        img_path = os.path.join(self.root_dir, file_name)
        image = img_path  # Pass path for tight_crop in Lambda
        if self.transform:
            image = self.transform(image)
        if self.category_ids is not None:
            label = self.category_ids[idx]
            return image, label, self.ids[idx]
        else:
            return image, self.ids[idx]

# Create full datasets
train_dataset = HerbariumDataset(train_df, 'nybg2020/train', transform=transform)
test_dataset = HerbariumDataset(test_df, 'nybg2020/test', transform=transform)

print('Train dataset size:', len(train_dataset))
print('Test dataset size:', len(test_dataset))

# Class distribution for weights
class_counts = Counter(train_df['category_id'])
num_classes = len(class_counts)
print(f'Number of unique classes: {num_classes}')
print(f'Min images per class: {min(class_counts.values())}')
print(f'Max images per class: {max(class_counts.values())}')

Train shape: (811623, 9)
Train columns: ['file_name', 'height', 'id', 'license', 'width', 'category_id', 'id_y', 'image_id', 'region_id']


Test shape: (219124, 5)
Test columns: ['file_name', 'height', 'id', 'license', 'width']
Train dataset size: 811623
Test dataset size: 219124
Number of unique classes: 32093
Min images per class: 1
Max images per class: 1412


In [3]:
import torch.nn as nn
import torch.nn.functional as F
from torchvision import models
from torch.utils.data import DataLoader
from torch.amp import autocast
from tqdm import tqdm
import numpy as np
import pickle
import os

# Enable cuDNN benchmark for speed
torch.backends.cudnn.benchmark = True

# Load model for embedding extraction (efficientnet_v2_s for speed)
model = models.efficientnet_v2_s(weights='DEFAULT')
model.classifier = nn.Identity()
model = model.cuda().eval()
print('Model loaded: efficientnet_v2_s with Identity classifier for embeddings')

# Extract train embeddings (full dataset, original only to save time/memory, save pkl)
if os.path.exists('train_embeddings.pkl'):
    print('Loading existing train_embeddings.pkl')
    with open('train_embeddings.pkl', 'rb') as f:
        train_data = pickle.load(f)
    train_embeddings_norm = train_data['embeddings']
    train_labels = train_data['labels']
    train_ids = train_data['ids']
    print(f'Loaded train embeddings shape: {train_embeddings_norm.shape}')
else:
    # Create DataLoader for full train (smaller batch 32, num_workers=0 to avoid OOM)
    train_loader = DataLoader(train_dataset, batch_size=32, shuffle=False, num_workers=0, pin_memory=True)

    # Extract original train embeddings with AMP
    train_embeddings_orig = []
    train_labels_list = []
    train_ids_list = []
    batch_count = 0
    with torch.no_grad():
        for images, labels, ids in tqdm(train_loader, desc='Extracting train embeddings (orig)'):
            images = images.cuda()
            with autocast('cuda'):
                emb = model(images)
                emb = emb.float()  # Ensure float32
            emb = F.normalize(emb, dim=1).cpu()
            train_embeddings_orig.append(emb)
            train_labels_list.extend(labels)
            train_ids_list.extend(ids)
            batch_count += 1
            if batch_count % 20 == 0:
                print(f'Processed {batch_count} batches, GPU memory: {torch.cuda.memory_allocated()/1e9:.1f}GB')
            if batch_count % 50 == 0:
                torch.cuda.empty_cache()
    train_embeddings_orig = torch.cat(train_embeddings_orig, dim=0).numpy()
    train_labels = np.array(train_labels_list)
    train_ids = np.array(train_ids_list)
    train_embeddings_norm = train_embeddings_orig  # No TTA for train to save time
    print(f'Train embeddings shape: {train_embeddings_norm.shape}')

    # Save train embeddings
    with open('train_embeddings.pkl', 'wb') as f:
        pickle.dump({'embeddings': train_embeddings_norm, 'labels': train_labels, 'ids': train_ids}, f)
    print('Saved train_embeddings.pkl')

# Extract test embeddings (TTA, save pkl)
if os.path.exists('test_embeddings.pkl'):
    print('Loading existing test_embeddings.pkl')
    with open('test_embeddings.pkl', 'rb') as f:
        test_data = pickle.load(f)
    test_embeddings_norm = test_data['embeddings']
    test_ids = test_data['ids']
    print(f'Loaded test embeddings shape: {test_embeddings_norm.shape}')
else:
    test_loader = DataLoader(test_dataset, batch_size=128, shuffle=False, num_workers=4, pin_memory=True)

    # Extract original test embeddings
    test_embeddings_orig = []
    test_ids_list = []
    with torch.no_grad():
        for images, ids in tqdm(test_loader, desc='Extracting test embeddings (orig)'):
            images = images.cuda()
            with autocast('cuda'):
                emb = model(images)
                emb = emb.float()
            emb = F.normalize(emb, dim=1).cpu()
            test_embeddings_orig.append(emb)
            test_ids_list.extend(ids)
    test_embeddings_orig = torch.cat(test_embeddings_orig, dim=0).numpy()
    test_ids = np.array(test_ids_list)

    # TTA flip for test
    test_dataset_flip = HerbariumDataset(test_df, 'nybg2020/test', transform=flip_transform)
    test_loader_flip = DataLoader(test_dataset_flip, batch_size=128, shuffle=False, num_workers=4, pin_memory=True)

    test_embeddings_flip = []
    with torch.no_grad():
        for images, _ in tqdm(test_loader_flip, desc='Extracting test embeddings (flip)'):
            images = images.cuda()
            with autocast('cuda'):
                emb = model(images)
                emb = emb.float()
            emb = F.normalize(emb, dim=1).cpu()
            test_embeddings_flip.append(emb)
    test_embeddings_flip = torch.cat(test_embeddings_flip, dim=0).numpy()

    # Average and normalize
    test_embeddings_avg_torch = (torch.from_numpy(test_embeddings_orig).float() + torch.from_numpy(test_embeddings_flip).float()) / 2
    test_embeddings_norm = F.normalize(test_embeddings_avg_torch, dim=1).float().numpy()

    # Save test embeddings
    with open('test_embeddings.pkl', 'wb') as f:
        pickle.dump({'embeddings': test_embeddings_norm, 'ids': test_ids}, f)
    print('Saved test_embeddings.pkl')

print(f'Final train embeddings shape: {train_embeddings_norm.shape}')
print(f'Final test embeddings shape: {test_embeddings_norm.shape}')

Model loaded: efficientnet_v2_s with Identity classifier for embeddings


Extracting train embeddings (orig):   0%|          | 0/25364 [00:00<?, ?it/s]

Extracting train embeddings (orig):   0%|          | 1/25364 [00:01<8:47:28,  1.25s/it]

Extracting train embeddings (orig):   0%|          | 2/25364 [00:01<5:31:42,  1.27it/s]

Extracting train embeddings (orig):   0%|          | 3/25364 [00:02<4:22:16,  1.61it/s]

...

Extracting test embeddings (flip): 100%|█████████▉| 1710/1712 [08:52<00:00,  3.61it/s]

Extracting test embeddings (flip): 100%|█████████▉| 1711/1712 [08:52<00:00,  3.48it/s]

Extracting test embeddings (flip): 100%|██████████| 1712/1712 [08:53<00:00,  3.14it/s]

Extracting test embeddings (flip): 100%|██████████| 1712/1712 [08:53<00:00,  3.21it/s]

Saved test_embeddings.pkl
Final train embeddings shape: (811623, 1280)
Final test embeddings shape: (219124, 1280)


In [4]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset
from torch.optim import AdamW
from torch.optim.lr_scheduler import CosineAnnealingLR
from torch.amp import autocast, GradScaler
from sklearn.metrics import f1_score
import numpy as np
import pandas as pd
import pickle
import os
from tqdm import tqdm
from collections import Counter
import random

# Load embeddings (assuming cell 2 completed)
with open('train_embeddings.pkl', 'rb') as f:
    train_data = pickle.load(f)
train_embeddings = train_data['embeddings']
train_labels = train_data['labels']
train_ids = train_data['ids']

with open('test_embeddings.pkl', 'rb') as f:
    test_data = pickle.load(f)
test_embeddings = test_data['embeddings']
test_ids = test_data['ids']

print(f'Train embeddings shape: {train_embeddings.shape}')
print(f'Test embeddings shape: {test_embeddings.shape}')

# Ensure L2 normalized
train_embeddings = F.normalize(torch.from_numpy(train_embeddings).float(), dim=1).numpy()
test_embeddings = F.normalize(torch.from_numpy(test_embeddings).float(), dim=1).numpy()

# Derive shapes from data
emb_dim = train_embeddings.shape[1]
num_classes = int(train_labels.max()) + 1
print(f'Embedding dim: {emb_dim}, Num classes: {num_classes}')

# Safe 90/10 split: per-class shuffle, max(1, floor(10%)) to val; <10 all to train
rng = np.random.RandomState(42)
train_idx = []
val_idx = []
class_counts = Counter(train_labels)
for cls, cnt in class_counts.items():
    idxs = np.where(train_labels == cls)[0]
    if cnt >= 10:
        perm = idxs[rng.permutation(len(idxs))]
        v = max(1, len(perm) // 10)
        val_idx.extend(perm[:v])
        train_idx.extend(perm[v:])
    else:
        train_idx.extend(idxs)
train_idx = np.array(train_idx)
val_idx = np.array(val_idx)
print(f'Train split size: {len(train_idx)}, Val size: {len(val_idx)}')

# Prepare datasets
train_emb_t = torch.from_numpy(train_embeddings[train_idx]).float()
train_lbl_t = torch.from_numpy(train_labels[train_idx]).long()
train_dataset = TensorDataset(train_emb_t, train_lbl_t)

val_emb_t = torch.from_numpy(train_embeddings[val_idx]).float()
val_lbl_t = torch.from_numpy(train_labels[val_idx]).long()
val_dataset = TensorDataset(val_emb_t, val_lbl_t)

# Compute class frequencies and log priors
class_freq = np.bincount(train_labels, minlength=num_classes)
log_priors = np.log(class_freq + 1e-8) - np.log(class_freq.sum() + 1e-8)

# Effective number weights
beta = 0.9999
effective_num = 1.0 - np.power(beta, class_freq)
weights = (1.0 - beta) / (effective_num + 1e-8)
weights = weights / weights.mean()
weights = np.clip(weights, 0.1, 10.0)
class_weights = torch.from_numpy(weights).float()

# DataLoaders
train_loader = DataLoader(train_dataset, batch_size=1024, shuffle=True, num_workers=4, pin_memory=True)
val_loader = DataLoader(val_dataset, batch_size=4096, shuffle=False, num_workers=4, pin_memory=True)

# Model: Linear with bias init from log priors
model = nn.Linear(emb_dim, num_classes).cuda()
with torch.no_grad():
    model.bias.copy_(torch.from_numpy(log_priors).float().cuda())
model = model.float()

# Loss and optimizer
criterion = nn.CrossEntropyLoss(weight=class_weights.cuda(), label_smoothing=0.1)
optimizer = AdamW(model.parameters(), lr=0.002, weight_decay=0.01)
scheduler = CosineAnnealingLR(optimizer, T_max=5)
scaler = GradScaler()

# Training loop
best_f1 = 0.0
best_model_state = None
epochs = 5
for epoch in range(epochs):
    model.train()
    train_loss = 0.0
    for batch_emb, batch_lbl in tqdm(train_loader, desc=f'Epoch {epoch+1}/{epochs} Train'):
        batch_emb, batch_lbl = batch_emb.cuda(), batch_lbl.cuda()
        optimizer.zero_grad()
        with autocast('cuda'):
            logits = model(batch_emb)
            loss = criterion(logits, batch_lbl)
        scaler.scale(loss).backward()
        scaler.step(optimizer)
        scaler.update()
        train_loss += loss.item()
    scheduler.step()
    print(f'Epoch {epoch+1} Train Loss: {train_loss / len(train_loader):.4f}')
    
    # Validation (no softmax needed)
    model.eval()
    val_preds = []
    val_trues = []
    with torch.no_grad():
        for batch_emb, batch_lbl in tqdm(val_loader, desc=f'Epoch {epoch+1}/{epochs} Val'):
            batch_emb, batch_lbl = batch_emb.cuda(), batch_lbl.cuda()
            with autocast('cuda'):
                logits = model(batch_emb)
                preds = torch.argmax(logits, dim=1)
            val_preds.extend(preds.cpu().numpy())
            val_trues.extend(batch_lbl.cpu().numpy())
    val_f1 = f1_score(val_trues, val_preds, average='macro')
    print(f'Epoch {epoch+1} Val Macro F1: {val_f1:.4f}')
    
    if val_f1 > best_f1:
        best_f1 = val_f1
        best_model_state = {k: v.detach().cpu().clone() for k, v in model.state_dict().items()}
    
    torch.cuda.empty_cache()

# Load best model
if best_model_state is not None:
    model.load_state_dict(best_model_state)
print(f'Best Val Macro F1: {best_f1:.4f}')

# Cache val logits and trues for tuning
model.eval()
val_logits_list = []
val_trues_list = []
with torch.no_grad():
    for batch_emb, batch_lbl in val_loader:
        batch_emb, batch_lbl = batch_emb.cuda(non_blocking=True), batch_lbl.cuda(non_blocking=True)
        with autocast('cuda'):
            logits = model(batch_emb).float().cpu()
        val_logits_list.append(logits)
        val_trues_list.append(batch_lbl.cpu())
val_logits = torch.cat(val_logits_list, dim=0)
val_trues = torch.cat(val_trues_list).numpy()
log_priors_cpu = torch.from_numpy(log_priors).float()

# Tune tau on cached val
best_tau = 0.0
best_tau_f1 = 0.0
for tau in [0.0, 0.25, 0.5, 0.75, 1.0]:
    adj = val_logits - tau * log_priors_cpu.unsqueeze(0)
    preds = adj.argmax(dim=1).numpy()
    f1 = f1_score(val_trues, preds, average='macro')
    print(f'Tau {tau}: Val Macro F1 {f1:.4f}')
    if f1 > best_tau_f1:
        best_tau_f1 = f1
        best_tau = tau

print(f'Best Tau: {best_tau}, F1: {best_tau_f1:.4f}')

# Compute prototypes: vectorized mean per class from full train
prototypes = np.zeros((num_classes, emb_dim), dtype=np.float32)
np.add.at(prototypes, train_labels, train_embeddings)
counts = np.bincount(train_labels, minlength=num_classes).astype(np.float32)
prototypes = prototypes / np.maximum(counts[:, np.newaxis], 1e-6)
proto_t = torch.from_numpy(prototypes).float().cuda()
proto_t = F.normalize(proto_t, dim=1)

# Precompute val cosine to prototypes for blend tuning
val_emb_cpu = torch.from_numpy(train_embeddings[val_idx]).float()
val_cos = val_emb_cpu @ proto_t.t().cpu()

# Tune blend a and s on val
s_grid = [20, 30]
a_grid = [0.5, 0.6, 0.7, 0.8, 0.9, 1.0]
best_f1_blend = best_tau_f1
best_a = 1.0
best_s = 30.0
for s in s_grid:
    for a in a_grid:
        adj = val_logits - best_tau * log_priors_cpu.unsqueeze(0)
        blended = a * adj + (1 - a) * (s * val_cos)
        preds = blended.argmax(dim=1).numpy()
        f1 = f1_score(val_trues, preds, average='macro')
        if f1 > best_f1_blend:
            best_f1_blend = f1
            best_a = a
            best_s = s
print(f'Best blend a: {best_a}, s: {best_s}, F1: {best_f1_blend:.4f}')

# Test inference: batched to avoid OOM
test_emb_t = torch.from_numpy(test_embeddings).float()
test_loader_inf = DataLoader(TensorDataset(test_emb_t), batch_size=4096, shuffle=False, num_workers=0)
preds_list = []
model.eval()
log_priors_cuda = torch.from_numpy(log_priors).float().cuda()
with torch.no_grad():
    for (xb,) in test_loader_inf:
        xb = xb.cuda(non_blocking=True)
        with autocast('cuda'):
            clf = model(xb).float()
        adj = clf - best_tau * log_priors_cuda.unsqueeze(0)
        cos = xb @ proto_t.t()
        blended = best_a * adj + (1 - best_a) * (best_s * cos)
        preds_list.append(blended.argmax(dim=1).cpu())
test_preds = torch.cat(preds_list).numpy()

# Create submission
submission = pd.DataFrame({'Id': test_ids, 'Predicted': test_preds})
submission = submission.sort_values('Id').reset_index(drop=True)
submission.to_csv('submission.csv', index=False)
print('Submission saved as submission.csv')
print(f'CV Macro F1 (blended): {best_f1_blend:.4f}')
print('Unique predicted classes:', len(np.unique(test_preds)))

Train embeddings shape: (811623, 1280)
Test embeddings shape: (219124, 1280)


Embedding dim: 1280, Num classes: 32094


Train split size: 743187, Val size: 68436


Epoch 1/5 Train:   0%|          | 0/726 [00:00<?, ?it/s]

Epoch 1/5 Train:   0%|          | 1/726 [00:01<12:14,  1.01s/it]

...

Tau 0.5: Val Macro F1 0.0052


Tau 0.75: Val Macro F1 0.0003


Tau 1.0: Val Macro F1 0.0001
Best Tau: 0.0, F1: 0.0420


Best blend a: 0.5, s: 30, F1: 0.1000


Submission saved as submission.csv
CV Macro F1 (blended): 0.1000
Unique predicted classes: 6872


In [5]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader, TensorDataset, WeightedRandomSampler
from torch.optim import AdamW
from torch.optim.lr_scheduler import CosineAnnealingLR
from torch.amp import autocast, GradScaler
from sklearn.metrics import f1_score
import numpy as np
import pandas as pd
import pickle
import os
from tqdm import tqdm
from collections import Counter
import random

# Assuming embeddings are already loaded from previous cell; reload if needed
with open('train_embeddings.pkl', 'rb') as f:
    train_data = pickle.load(f)
train_embeddings = train_data['embeddings']
train_labels = train_data['labels']
train_ids = train_data['ids']

with open('test_embeddings.pkl', 'rb') as f:
    test_data = pickle.load(f)
test_embeddings = test_data['embeddings']
test_ids = test_data['ids']

print(f'Train embeddings shape: {train_embeddings.shape}')
print(f'Test embeddings shape: {test_embeddings.shape}')

# Ensure L2 normalized
train_embeddings = F.normalize(torch.from_numpy(train_embeddings).float(), dim=1).numpy()
test_embeddings = F.normalize(torch.from_numpy(test_embeddings).float(), dim=1).numpy()

# Fix: Compute num_classes correctly and remap labels to contiguous 0 to num_classes-1
unique_labels = np.unique(train_labels)
num_classes = len(unique_labels)
label_to_idx = {label: idx for idx, label in enumerate(sorted(unique_labels))}
remapped_labels = np.array([label_to_idx[label] for label in train_labels])
print(f'Fixed num_classes: {num_classes} (unique labels)')

# Derive shapes
emb_dim = train_embeddings.shape[1]
print(f'Embedding dim: {emb_dim}')

# Safe 90/10 split on remapped labels
rng = np.random.RandomState(42)
train_idx = []
val_idx = []
class_counts = Counter(remapped_labels)
for cls, cnt in class_counts.items():
    idxs = np.where(remapped_labels == cls)[0]
    if cnt >= 10:
        perm = idxs[rng.permutation(len(idxs))]
        v = max(1, len(perm) // 10)
        val_idx.extend(perm[:v])
        train_idx.extend(perm[v:])
    else:
        train_idx.extend(idxs)
train_idx = np.array(train_idx)
val_idx = np.array(val_idx)
print(f'Train split size: {len(train_idx)}, Val size: {len(val_idx)}')

# Prepare datasets with remapped labels
train_emb_t = torch.from_numpy(train_embeddings[train_idx]).float()
train_lbl_t = torch.from_numpy(remapped_labels[train_idx]).long()
train_dataset = TensorDataset(train_emb_t, train_lbl_t)

val_emb_t = torch.from_numpy(train_embeddings[val_idx]).float()
val_lbl_t = torch.from_numpy(remapped_labels[val_idx]).long()
val_dataset = TensorDataset(val_emb_t, val_lbl_t)

# Effective number weights for alpha in Focal Loss
class_freq = np.bincount(remapped_labels, minlength=num_classes)
beta = 0.9999
effective_num = 1.0 - np.power(beta, class_freq)
alpha = (1.0 - beta) / (effective_num + 1e-8)
alpha = alpha / alpha.mean()
alpha = np.clip(alpha, 0.1, 10.0)
class_weights = torch.from_numpy(alpha).float()

# WeightedRandomSampler for class-balanced batches
class_sample_counts = np.bincount(remapped_labels[train_idx], minlength=num_classes)
class_sample_counts = np.maximum(class_sample_counts, 1)
num_samples = len(train_idx)
labels_train = remapped_labels[train_idx]
sample_weights = np.array([1.0 / class_sample_counts[label] for label in labels_train])
sampler = WeightedRandomSampler(sample_weights, num_samples=num_samples, replacement=True)

# DataLoaders with sampler
train_loader = DataLoader(train_dataset, batch_size=1024, sampler=sampler, num_workers=4, pin_memory=True)
val_loader = DataLoader(val_dataset, batch_size=4096, shuffle=False, num_workers=4, pin_memory=True)

# Cosine Classifier: L2-normalized features and weights with learnable scale
class CosineClassifier(nn.Module):
    def __init__(self, in_features, out_features, scale=1.0):
        super().__init__()
        self.in_features = in_features
        self.out_features = out_features
        self.weight = nn.Parameter(torch.randn(out_features, in_features))
        self.scale = nn.Parameter(torch.tensor(scale))

    def forward(self, input):
        # L2 normalize input and weight
        input_norm = F.normalize(input, dim=1)
        weight_norm = F.normalize(self.weight, dim=1)
        # Cosine similarity
        cosine = torch.mm(input_norm, weight_norm.t())
        # Scale and return
        return self.scale * cosine

model = CosineClassifier(emb_dim, num_classes, scale=30.0).cuda()
model = model.float()

# Focal Loss implementation
class FocalLoss(nn.Module):
    def __init__(self, alpha=None, gamma=2.0, reduction='mean'):
        super().__init__()
        self.alpha = alpha
        self.gamma = gamma
        self.reduction = reduction

    def forward(self, inputs, targets):
        ce_loss = F.cross_entropy(inputs, targets, reduction='none', weight=self.alpha)
        pt = torch.exp(-ce_loss)
        focal_loss = (1 - pt) ** self.gamma * ce_loss
        if self.reduction == 'mean':
            return focal_loss.mean()
        elif self.reduction == 'sum':
            return focal_loss.sum()
        return focal_loss

criterion = FocalLoss(alpha=class_weights.cuda(), gamma=2.0)

# Optimizer with higher LR
optimizer = AdamW(model.parameters(), lr=0.01, weight_decay=0.01)
scheduler = CosineAnnealingLR(optimizer, T_max=5)
scaler = GradScaler()

# Training loop (5 epochs)
best_f1 = 0.0
best_model_state = None
epochs = 5
for epoch in range(epochs):
    model.train()
    train_loss = 0.0
    for batch_emb, batch_lbl in tqdm(train_loader, desc=f'Epoch {epoch+1}/{epochs} Train'):
        batch_emb, batch_lbl = batch_emb.cuda(), batch_lbl.cuda()
        optimizer.zero_grad()
        with autocast('cuda'):
            logits = model(batch_emb)
            loss = criterion(logits, batch_lbl)
        scaler.scale(loss).backward()
        scaler.step(optimizer)
        scaler.update()
        train_loss += loss.item()
    scheduler.step()
    print(f'Epoch {epoch+1} Train Loss: {train_loss / len(train_loader):.4f}')
    
    # Validation
    model.eval()
    val_preds = []
    val_trues = []
    with torch.no_grad():
        for batch_emb, batch_lbl in tqdm(val_loader, desc=f'Epoch {epoch+1}/{epochs} Val'):
            batch_emb, batch_lbl = batch_emb.cuda(), batch_lbl.cuda()
            with autocast('cuda'):
                logits = model(batch_emb)
                preds = torch.argmax(logits, dim=1)
            val_preds.extend(preds.cpu().numpy())
            val_trues.extend(batch_lbl.cpu().numpy())
    val_f1 = f1_score(val_trues, val_preds, average='macro')
    print(f'Epoch {epoch+1} Val Macro F1: {val_f1:.4f}')
    
    if val_f1 > best_f1:
        best_f1 = val_f1
        best_model_state = {k: v.detach().cpu().clone() for k, v in model.state_dict().items()}
    
    torch.cuda.empty_cache()

# Load best model
if best_model_state is not None:
    model.load_state_dict(best_model_state)
print(f'Best Val Macro F1: {best_f1:.4f}')

# Reuse post-processing from cell 3: cache val logits, tune tau, compute prototypes, tune blend
# Note: For prototypes, use remapped labels but map back to original for submission
# Compute prototypes on remapped
prototypes = np.zeros((num_classes, emb_dim), dtype=np.float32)
np.add.at(prototypes, remapped_labels, train_embeddings)
counts = np.bincount(remapped_labels, minlength=num_classes).astype(np.float32)
prototypes = prototypes / np.maximum(counts[:, np.newaxis], 1e-6)
proto_t = torch.from_numpy(prototypes).float().cuda()
proto_t = F.normalize(proto_t, dim=1)

# Cache val logits and trues (remapped)
model.eval()
val_logits_list = []
val_trues_list = []
with torch.no_grad():
    for batch_emb, batch_lbl in val_loader:
        batch_emb, batch_lbl = batch_emb.cuda(non_blocking=True), batch_lbl.cuda(non_blocking=True)
        with autocast('cuda'):
            logits = model(batch_emb).float().cpu()
        val_logits_list.append(logits)
        val_trues_list.append(batch_lbl.cpu())
val_logits = torch.cat(val_logits_list, dim=0)
val_trues = torch.cat(val_trues_list).numpy()

# For tau tuning, need log priors on remapped classes (assuming uniform or freq-based)
class_freq_remap = np.bincount(remapped_labels, minlength=num_classes)
log_priors = np.log(class_freq_remap + 1e-8) - np.log(class_freq_remap.sum() + 1e-8)
log_priors_cpu = torch.from_numpy(log_priors).float()

# Tune tau
best_tau = 0.0
best_tau_f1 = 0.0
for tau in [0.0, 0.25, 0.5, 0.75, 1.0]:
    adj = val_logits - tau * log_priors_cpu.unsqueeze(0)
    preds = adj.argmax(dim=1).numpy()
    f1 = f1_score(val_trues, preds, average='macro')
    print(f'Tau {tau}: Val Macro F1 {f1:.4f}')
    if f1 > best_tau_f1:
        best_tau_f1 = f1
        best_tau = tau

print(f'Best Tau: {best_tau}, F1: {best_tau_f1:.4f}')

# Precompute val cosine to prototypes
val_emb_cpu = torch.from_numpy(train_embeddings[val_idx]).float()
val_cos = val_emb_cpu @ proto_t.t().cpu()

# Tune blend a and s
s_grid = [20, 30]
a_grid = [0.5, 0.6, 0.7, 0.8, 0.9, 1.0]
best_f1_blend = best_tau_f1
best_a = 1.0
best_s = 30.0
for s in s_grid:
    for a in a_grid:
        adj = val_logits - best_tau * log_priors_cpu.unsqueeze(0)
        blended = a * adj + (1 - a) * (s * val_cos)
        preds = blended.argmax(dim=1).numpy()
        f1 = f1_score(val_trues, preds, average='macro')
        if f1 > best_f1_blend:
            best_f1_blend = f1
            best_a = a
            best_s = s
print(f'Best blend a: {best_a}, s: {best_s}, F1: {best_f1_blend:.4f}')

# Test inference with remapped
test_emb_t = torch.from_numpy(test_embeddings).float()
test_loader_inf = DataLoader(TensorDataset(test_emb_t), batch_size=4096, shuffle=False, num_workers=0)
preds_list = []
model.eval()
log_priors_cuda = torch.from_numpy(log_priors).float().cuda()
with torch.no_grad():
    for (xb,) in test_loader_inf:
        xb = xb.cuda(non_blocking=True)
        with autocast('cuda'):
            clf = model(xb).float()
        adj = clf - best_tau * log_priors_cuda.unsqueeze(0)
        cos = xb @ proto_t.t()
        blended = best_a * adj + (1 - best_a) * (best_s * cos)
        preds_list.append(blended.argmax(dim=1).cpu())
test_preds_remapped = torch.cat(preds_list).numpy()

# Map back to original labels
idx_to_label = {idx: label for label, idx in label_to_idx.items()}
test_preds_original = np.array([idx_to_label[idx] for idx in test_preds_remapped])

# Create submission
submission = pd.DataFrame({'Id': test_ids, 'Predicted': test_preds_original})
submission = submission.sort_values('Id').reset_index(drop=True)
submission.to_csv('submission.csv', index=False)
print('Submission saved as submission.csv')
print(f'CV Macro F1 (blended): {best_f1_blend:.4f}')
print('Unique predicted classes:', len(np.unique(test_preds_original)))

Train embeddings shape: (811623, 1280)
Test embeddings shape: (219124, 1280)


Fixed num_classes: 32093 (unique labels)
Embedding dim: 1280


Train split size: 743187, Val size: 68436


Epoch 1/5 Train:   0%|          | 0/726 [00:00<?, ?it/s]

Epoch 1/5 Train:   0%|          | 1/726 [00:00<10:28,  1.15it/s]

...

Tau 0.5: Val Macro F1 0.0216


Tau 0.75: Val Macro F1 0.0155


Tau 1.0: Val Macro F1 0.0115
Best Tau: 0.0, F1: 0.0434


Best blend a: 0.5, s: 30, F1: 0.0745


Submission saved as submission.csv
CV Macro F1 (blended): 0.0745
Unique predicted classes: 25575
